### Registering entities represented in grocery dataset

In FeatureByte, an "entity" models real-world objects and ideas. These entities often correspond to columns in database tables.

Taking our grocery scenario as an example, we can view "Customer", "Invoice", and "Item" as entities.

To help FeatureByte identify these entities in the data and the columns that represent them, we'll be creating and tagging these entities in this tutorial.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

21:56:55 | INFO     | Using configuration file at: /Users/gxav/.featurebyte/config.yaml


21:56:55 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


21:56:55 | WARNING  | Remote SDK version (0.5.0.dev6) is different from local (0.5.0.dev1). Update local SDK to avoid unexpected behavior.


21:56:55 | INFO     | No catalog activated.


21:56:56 | INFO     | 6 feature lists, 31 features deployed


...

21:56:56 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


21:56:56 | WARNING  | Remote SDK version (0.5.0.dev6) is different from local (0.5.0.dev1). Update local SDK to avoid unexpected behavior.


21:56:56 | INFO     | No catalog activated.


21:56:57 | INFO     | 6 feature lists, 31 features deployed


21:56:57 | INFO     | Catalog activated: Grocery Dataset Tutorial


As previously discussed, we'll establish the following entities:
- customer - an individual shopping at the stores
- invoice - a record of the customer's purchase
- item - individual items on the invoice
- product - products available in the store for purchase
- productgroup - the category or group a product falls under
- frenchstate - a region in France (since our dataset revolves around French grocery stores and their customers)

It's worth noting that the count of entities doesn't necessarily have to align with the number of tables. An entity is a business-oriented term, and multiple entities might be represented within a single table.

When creating an entity, you'll need to define its [serving name](https://docs.featurebyte.com/0.5/about/glossary/#entity-serving-name). This name acts as a unique identifier, particularly during preview or serving requests.

In [2]:
catalog.create_entity(name="customer", serving_names=["GROCERYCUSTOMERGUID"])
catalog.create_entity(name="invoice", serving_names=["GROCERYINVOICEGUID"])
catalog.create_entity(name="item", serving_names=["GROCERYINVOICEITEMGUID"])
catalog.create_entity(name="product", serving_names=["GROCERYPRODUCTGUID"])
catalog.create_entity(name="productgroup", serving_names=["PRODUCTGROUP"])
catalog.create_entity(name="frenchstate", serving_names=["FRENCHSTATE"])

<featurebyte.api.entity.Entity at 0x7fe5f812a880>
{
  'name': 'frenchstate',
  'created_at': '2023-09-11T13:57:04.775000',
  'updated_at': None,
  'description': None,
  'serving_names': [
    'FRENCHSTATE'
  ],
  'catalog_name': 'Grocery Dataset Tutorial'
}

Now that we've established the entities, it's time to guide FeatureByte in mapping these entities to the actual data in our tables.

In [3]:
customer_table = catalog.get_table("GROCERYCUSTOMER")
invoice_table = catalog.get_table("GROCERYINVOICE")
items_table = catalog.get_table("INVOICEITEMS")
product_table = catalog.get_table("GROCERYPRODUCT")

In [4]:
# tag the entities for the grocery customer table
customer_table.GroceryCustomerGuid.as_entity("customer")
customer_table.State.as_entity("frenchstate")

# tag the entities for the grocery invoice table
invoice_table.GroceryInvoiceGuid.as_entity("invoice")
invoice_table.GroceryCustomerGuid.as_entity("customer")

# tag the entities for the grocery items table
items_table.GroceryInvoiceItemGuid.as_entity("item")
items_table.GroceryInvoiceGuid.as_entity("invoice")
items_table.GroceryProductGuid.as_entity("product")

# tag the entities for the grocery product table
product_table.GroceryProductGuid.as_entity("product")
product_table.ProductGroup.as_entity("productgroup")

Now, if we list the tables as we did in the previous tutorial, we'll notice that entities have been assigned to each table.

In [5]:
display(catalog.list_tables())

id             name             type        status  \
0  64ff1c940d5bfbfb21bce78c   GROCERYPRODUCT  dimension_table  PUBLIC_DRAFT   
1  64ff1c920d5bfbfb21bce78b     INVOICEITEMS       item_table  PUBLIC_DRAFT   
2  64ff1c910d5bfbfb21bce78a   GROCERYINVOICE      event_table  PUBLIC_DRAFT   
3  64ff1c8f0d5bfbfb21bce789  GROCERYCUSTOMER        scd_table  PUBLIC_DRAFT   

                   entities                  created_at  
0   [product, productgroup]  2023-09-11T13:56:37.144000  
1  [item, invoice, product]  2023-09-11T13:56:35.927000  
2       [invoice, customer]  2023-09-11T13:56:34.182000  
3   [customer, frenchstate]  2023-09-11T13:56:32.993000

We can also list entities separately: 

In [6]:
display(catalog.list_entities())

id          name             serving_names  \
0  64ff1caf36a87a52b58efae1   frenchstate             [FRENCHSTATE]   
1  64ff1cae36a87a52b58efae0  productgroup            [PRODUCTGROUP]   
2  64ff1cad36a87a52b58efadf       product      [GROCERYPRODUCTGUID]   
3  64ff1cab36a87a52b58efade          item  [GROCERYINVOICEITEMGUID]   
4  64ff1caa36a87a52b58efadd       invoice      [GROCERYINVOICEGUID]   
5  64ff1ca936a87a52b58efadc      customer     [GROCERYCUSTOMERGUID]   

                   created_at  
0  2023-09-11T13:57:04.775000  
1  2023-09-11T13:57:03.544000  
2  2023-09-11T13:57:02.300000  
3  2023-09-11T13:57:01.116000  
4  2023-09-11T13:56:59.974000  
5  2023-09-11T13:56:58.863000

And let's examine the relationships between entities, which FeatureByte has conveniently outlined for us:

In [7]:
display(catalog.list_relationships())

id relationship_type    entity related_entity  \
0  64ff1cc20290c0ac6f31785d      child_parent   product   productgroup   
1  64ff1cc0c0038ba1e4252611      child_parent      item        product   
2  64ff1cbec0038ba1e425260c      child_parent      item        invoice   
3  64ff1cbc0290c0ac6f317855      child_parent   invoice       customer   
4  64ff1cbac0038ba1e4252605      child_parent  customer    frenchstate   

    relation_table relation_table_type  enabled                  created_at  \
0   GROCERYPRODUCT     dimension_table     True  2023-09-11T13:57:22.828000   
1     INVOICEITEMS          item_table     True  2023-09-11T13:57:20.107000   
2     INVOICEITEMS          item_table     True  2023-09-11T13:57:18.965000   
3   GROCERYINVOICE         event_table     True  2023-09-11T13:57:16.978000   
4  GROCERYCUSTOMER           scd_table     True  2023-09-11T13:57:14.789000   

  updated_at  
0       None  
1       None  
2       None  
3       None  
4       None

That's it for most important data modeling concepts in FeatureByte. 
In next tutorials we will look into concepts related to data cleaning and feature engineering. 

### For more details about concepts we discussed in this tutorial, feel free to explore:
- [More info on Entities](https://docs.featurebyte.com/latest/about/glossary/#related-to-entities)

#### SDK reference for
- [Entity](https://docs.featurebyte.com/latest/reference/core/entity/)
- [Catalog.create_entity()](https://docs.featurebyte.com/latest/reference/featurebyte.api.catalog.Catalog.create_entity/)
- [TableColumn.as_entity()](https://docs.featurebyte.com/latest/reference/featurebyte.api.base_table.TableColumn.as_entity/)